
# Pareto front

In this example, we illustrate the use of the :class:`.ParetoFront` plot
on the Sobieski's SSBJ problem.


In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo.problems.sobieski.core.problem import SobieskiProblem

## Import
The first step is to import some high-level functions
and a method to get the design space.



In [ ]:
configure_logger()

## Description

The :class:`.ParetoFront` post-processing generates
a plot or a matrix of plots (if there are more than
2 objectives). It indicates in red the locally nondominated points for the
current objectives, and in green the globally (all objectives) Pareto optimal
points.



## Create disciplines
At this point, we instantiate the disciplines of Sobieski's SSBJ problem:
Propulsion, Aerodynamics, Structure and Mission



In [ ]:
disciplines = create_discipline(
    [
        "SobieskiPropulsion",
        "SobieskiAerodynamics",
        "SobieskiStructure",
        "SobieskiMission",
    ]
)

## Create design space
We also read the design space from the :class:`.SobieskiProblem`.



In [ ]:
design_space = SobieskiProblem().design_space

## Create and execute scenario
The next step is to build an MDO scenario in order to maximize the range,
encoded 'y_4', with respect to the design parameters, while satisfying the
inequality constraints 'g_1', 'g_2' and 'g_3'. We can use the MDF formulation,
the SLSQP optimization algorithm
and a maximum number of iterations equal to 100.



In [ ]:
scenario = create_scenario(
    disciplines,
    formulation="MDF",
    objective_name="y_4",
    maximize_objective=True,
    design_space=design_space,
)
scenario.set_differentiation_method()
for constraint in ["g_1", "g_2", "g_3"]:
    scenario.add_constraint(constraint, "ineq")
scenario.execute({"algo": "SLSQP", "max_iter": 10})

## Post-process scenario
Lastly, we post-process the scenario by means of the :class:`.ParetoFront`.



.. tip::

   Each post-processing method requires different inputs and offers a variety
   of customization options. Use the high-level function
   :func:`.get_post_processing_options_schema` to print a table with
   the options for any post-processing algorithm.
   Or refer to our dedicated page:
   `gen_post_algos`.



In [ ]:
scenario.post_process("ParetoFront", objectives=["g_3", "-y_4"], save=False, show=True)